In [3]:
import math

from sp_soccer_lib import create_team_df_dict
from sp_soccer_lib.championships import load_country, team_stats

In [22]:
def simulate_team(
    team: str,
    country_team_df,
    period: str,
    bet_progr: list,
    threshold: int,
    bet_span: int,
    match_details: bool = False,
):
    team_matches_df = country_team_df[team]
    team_matches_df = team_matches_df[team_matches_df["period"] == period]
    # print(team_matches_df.head())

    team_bet = 0
    team_wins = 0

    next_bet = 0
    for _, match in team_matches_df.iterrows():
        odds = 3 if math.isnan(match["B365D"]) else match["B365D"]

        # print(type(odds))
        # print(row)
        if match_details:
            print('--------------------------------')
            print(f'Match is {match["HomeTeam"]}-{match["AwayTeam"]}. Draw gives {odds}. Result for {team} is {match["result"]}')
        if next_bet:
            team_bet = team_bet + bet_progr[next_bet - 1]
            if match_details:
                print(f'!!! This is bet No {next_bet}. Betting {bet_progr[next_bet-1]} Eur.  !!!')
        else:
            if match_details:
                print('!!! No bet this time !!!')
            pass
        if match["FTR"] == "D":
            if next_bet:
                if match_details:
                    print(f'Colourful Ballons!!! We retrieve {bet_progr[next_bet - 1] * odds}')
                team_wins = team_wins + bet_progr[next_bet - 1] * odds
            next_bet = 0
        else:
            if (
                match["count_no_draw"] >= threshold
                and match["count_no_draw"] < threshold + bet_span
            ):
                next_bet = match["count_no_draw"] - threshold + 1
            else:
                next_bet = 0

        # if row['count_no_draw'] == threshold:
        #     next_bet = 1

    # print(f'{team} bet for {period}: {team_bet}')
    # print(f'{team} wins for {period}: {team_wins}')
    return team_bet, team_wins

In [23]:
country = 'greece'
# period = '2122'
# threshold = 6
# bet_span = 10
# bet_progr = [2,4,8, 16, 32, 64, 128, 256, 512, 1024]
bet_progr = [2,4,6, 9, 13, 20, 30, 45, 68, 103]
# bet_progr = [2,4,8, 16, 32, 64, 128, 256, 512, 1024]
# bet_progr = [2,4,8, 16, 32, 64, 128, 256, 512, 1024]

match_details = True

df = load_country(country)
# print(df.head(2))
team_df = create_team_df_dict(df)
# print(team_df)
stats_df = team_stats(team_df)
# print(stats_df.head(2))
total_bet = 0
total_wins = 0
team_result = []
period_result = []
for country in ['greece', 'italy']:
    for threshold in [3, 4, 5, 6]:
        for bet_span in [3, 4, 5, 6, 7, 8, 9, 10]:
            for period in ['2021', '2122']:
                for _, team_row in stats_df.iterrows():
                    print(f'Team:{team_row.name}, period:{period}, threshold:{threshold}, betspan:{bet_span}')
                    team = team_row.name
                    team_bet, team_wins = simulate_team(team, team_df, period, bet_progr, threshold, bet_span, match_details)
                    total_bet = total_bet + team_bet
                    total_wins = total_wins + team_wins
                    team_result.append({'country': country, 'period': period, 'threshold': threshold, 'span': bet_span, 'team': team, 'bet': team_bet, 'wins': team_wins})

                print(f'Total bet: {total_bet}')
                print(f'Total wins: {total_wins}')
                period_result.append({'country': country, 'period': period, 'threshold': threshold, 'span': bet_span, 'total_bet': total_bet, 'total_wins': total_wins})
                total_bet = 0
                total_wins = 0
print(team_result)
print(period_result)

c:\code\python\soccer\sp_soccer_lib\championships.py:25: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  load = pd.read_csv('https://www.football-data.co.uk/mmz4281/' + period + '/' + cfg.COUNTRIES[country] + '.csv',
c:\code\python\soccer\sp_soccer_lib\championships.py:25: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  load = pd.read_csv('https://www.football-data.co.uk/mmz4281/' + period + '/' + cfg.COUNTRIES[country] + '.csv',
c:\code\python\soccer\sp_soccer_lib\championships.py:25: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  lo

Team:Olympiakos, period:2021, threshold:3, betspan:3
--------------------------------
Match is Olympiakos-Asteras Tripolis. Draw gives 6.0. Result for Olympiakos is W
!!! No bet this time !!!
--------------------------------
Match is Olympiakos-Panetolikos. Draw gives 5.75. Result for Olympiakos is W
!!! No bet this time !!!
--------------------------------
Match is Giannina-Olympiakos. Draw gives 4.75. Result for Olympiakos is D
!!! No bet this time !!!
--------------------------------
Match is Olympiakos-Atromitos. Draw gives 4.75. Result for Olympiakos is W
!!! No bet this time !!!
--------------------------------
Match is Olympiakos-Apollon. Draw gives 8.5. Result for Olympiakos is W
!!! No bet this time !!!
--------------------------------
Match is OFI Crete-Olympiakos. Draw gives 5.25. Result for Olympiakos is W
!!! No bet this time !!!
Κουβάς (bucket...)
--------------------------------
Match is Olympiakos-Panathinaikos. Draw gives 4.2. Result for Olympiakos is W
!!! This is bet

In [25]:
import pandas as pd

pd.DataFrame.from_dict(team_result).to_excel('team.xlsx')
pd.DataFrame.from_dict(period_result).to_excel('period.xlsx')